In [1]:
import pandas as pd
import requests
from joblib import dump, load
from scipy import stats
from sklearn.manifold import Isomap

from vcub_keeper.config import ROOT_DIR

# from vcub_keeper.reader.reader import re
from vcub_keeper.reader.reader_utils import filter_periode

# from vcub_keeper.visualisation import *
from vcub_keeper.transform.features_factory import get_transactions_all, get_transactions_in, get_transactions_out

%load_ext autoreload
%autoreload 2

pd.options.display.max_rows = 500
pd.options.display.max_columns = 500

# Objectifs

- Obtenir les données depuis l'api de Damien
- Structuré ces données pour les utiliser avec le pipeline de prédiction

# Get data from API

## API Oslandia

### Dev

In [30]:
station_id=25
#station_id="25,102"
start_date='2021-10-14'
stop_date='2021-10-20'

#url = "http://data.oslandia.io/bikes/api/bordeaux/timeseries/station/106?start=2020-10-09&stop=2020-10-17"

url = \
    "http://data.oslandia.io/bikes/api/bordeaux/timeseries/station/"+ str(station_id) +\
    "?start=" + start_date + "&stop=" + stop_date
    
response = requests.get(url)

In [31]:
url

'http://data.oslandia.io/bikes/api/bordeaux/timeseries/station/25?start=2021-10-14&stop=2021-10-20'

In [ ]:
response.json()

In [ ]:
station_df = pd.DataFrame(response.json()['data'][0])

In [5]:
station_df.id.unique()

array(['25'], dtype=object)

In [6]:
# Status mapping
status_dict = {'open' : 1,
               'closed' : 0
              }
station_df['status'] = station_df['status'].map(status_dict)
station_df['status'] = station_df['status'].astype('uint8')

# Naming
station_df.rename(columns={'id':'station_id'}, inplace=True)
station_df.rename(columns={'ts':'date'}, inplace=True)

# Casting date & sorting DataFrame on station_id & date
station_df['date'] = pd.to_datetime(station_df['date'])
station_df = station_df.sort_values(['station_id', 'date'], ascending=[1, 1])

# Reset index
station_df = station_df.reset_index(drop=True)

# Dropduplicate station_id / date rows
station_df = station_df.drop_duplicates(subset=['station_id', 'date']).reset_index(drop=True)

# Create features
station_df = get_transactions_in(station_df)
station_df = get_transactions_out(station_df)
station_df = get_transactions_all(station_df)

In [7]:
station_df.tail(10)

available_bikes  available_stands station_id                 name  \
1619                0                 0         25  François de Sourdis   
1620                0                 0         25  François de Sourdis   
1621                0                 0         25  François de Sourdis   
1622                0                 0         25  François de Sourdis   
1623                0                 0         25  François de Sourdis   
1624                0                 0         25  François de Sourdis   
1625                0                 0         25  François de Sourdis   
1626                0                 0         25  François de Sourdis   
1627                0                 0         25  François de Sourdis   
1628                0                 0         25  François de Sourdis   

      nb_stands  status                date  transactions_in  \
1619         14       0 2020-10-19 23:13:13              0.0   
1620         14       0 2020-10-19 23:18:13              0.0   
1621         14       0 2020-10-19 23:24:13              0.0   
1622         14       0 2020-10-19 23:29:13              0.0   
1623         14       0 2020-10-19 23:33:13              0.0   
1624         14       0 2020-10-19 23:37:13              0.0   
1625         14       0 2020-10-19 23:42:13              0.0   
1626         14       0 2020-10-19 23:47:13              0.0   
1627         14       0 2020-10-19 23:53:13              0.0   
1628         14       0 2020-10-19 23:57:13              0.0   

      transactions_out  transactions_all  
1619               0.0               0.0  
1620               0.0               0.0  
1621               0.0               0.0  
1622               0.0               0.0  
1623               0.0               0.0  
1624               0.0               0.0  
1625               0.0               0.0  
1626               0.0               0.0  
1627               0.0               0.0  
1628               0.0               0.0

### Industrialisation

In [5]:
from vcub_keeper.config import ROOT_DATA_REF, THRESHOLD_PROFILE_STATION
from vcub_keeper.reader.reader import read_station_profile

#THRESHOLD_PROFILE_STATION = 0.3

station_profile = read_station_profile(path_directory=ROOT_DATA_REF)

stations_id_to_pred = \
    station_profile[station_profile['mean'] >= THRESHOLD_PROFILE_STATION]['station_id'].unique()

In [6]:
type(stations_id_to_pred)

numpy.ndarray

In [7]:
','.join(map(str, stations_id_to_pred))

'124,15,60,18,10,68,130,2,105,120,11,110,9,23,3,16,20,136,42,21,131,59,45,172,6,24,36,108,19,125,135,37,139,99,28,57,7,98,8,41,40,58,55,109,1,4,100,134,174,101,56,104,43,54,44,102,133,103,5,127,65,22,123,39,106'

In [18]:
import numpy as np
import requests


def get_data_from_api_by_station(station_id, start_date, stop_date):
    """
    Permet d'obtenir les données d'activité d'une station via une API
    
    Parameters
    ----------
    station_id : Int or List
        Numéro de la station de Vcub
    start_date : str
        Date de début de la Time Serie
    stop_date : str
        Date de fin de la Time Serie
    
    Returns
    -------
    Time serie in Json format
        
    Examples
    --------
    
    station_json = get_data_from_api_by_station(station_id=19, 
                                                start_date='2020-10-14',
                                                stop_date='2020-10-17')
    """
    
    if isinstance(station_id, list | np.ndarray):
        station_id = ','.join(map(str, station_id))
    
    url = \
        "http://data.oslandia.io/bikes/api/bordeaux/timeseries/station/"+ str(station_id) +\
        "?start=" + start_date + "&stop=" + stop_date
    
    response = requests.get(url)
    return response.json()

def transform_json_station_data_to_df(station_json):
    """
    Tranforme la Time Serie d'activité d'une ou plusieurs station en DataFrame
    Effectue plusieurs transformation comme la fonction create/creator.py 
    create_activity_time_series()
        - Structuration
        - Naming
        - Ajout de variables
        - Resampling sur 10min
    
    Parameters
    ----------
    station_json : json
        Time serie au format json de l'activité d'une station (ou plusieurs)
    Returns
    -------
    station_df_resample : DataFrame
        Time serie au format DataFrame de l'activité d'une ou plusieurs station
        resampler sur 10 min.
        
    Examples
    --------
    
    station_df = transform_json_station_data_to_df(station_json)
    
    """
    
    # Si il y a plusieurs stations dans le json
    if len(station_json['data']) > 1:
        station_df = pd.DataFrame()
        for i in range(0, len(station_json['data'])):
            temp_station_df = pd.DataFrame(station_json['data'][i])
            station_df = pd.concat([station_df, temp_station_df])
    # Il y une seule station dans le json
    else:        
        station_df = pd.DataFrame(station_json['data'][0])
    
    # Status mapping
    status_dict = {'open' : 1,
                   'closed' : 0
                  }
    station_df['status'] = station_df['status'].map(status_dict)
    station_df['status'] = station_df['status'].astype('uint8')

    # Naming
    station_df.rename(columns={'id':'station_id'}, inplace=True)
    station_df.rename(columns={'ts':'date'}, inplace=True)

    # Casting & sorting DataFrame on station_id & date
    station_df['date'] = pd.to_datetime(station_df['date'])
    station_df['station_id'] = station_df['station_id'].astype(int)
    station_df = station_df.sort_values(['station_id', 'date'], ascending=[1, 1])

    # Reset index
    station_df = station_df.reset_index(drop=True)

    # Dropduplicate station_id / date rows
    station_df = station_df.drop_duplicates(subset=['station_id', 'date']).reset_index(drop=True)

    # Create features
    station_df = get_transactions_in(station_df)
    station_df = get_transactions_out(station_df)
    station_df = get_transactions_all(station_df)

    ## Resampling

    # cf Bug Pandas : https://github.com/pandas-dev/pandas/issues/33548
    station_df = station_df.set_index('date')

    station_df_resample = \
        station_df.groupby('station_id').resample('10T', 
                                                  label='right',
                                                 ).agg({'available_stands' : 'last',
                                                        'available_bikes' : 'last',
                                                        'status' : 'max', # Empeche les micro déconnection à la station
                                                        'transactions_in' : 'sum',
                                                        'transactions_out' : 'sum',
                                                        'transactions_all' : 'sum'}).reset_index()
    return station_df_resample

In [19]:
station_id='19'
#station_id=[19, 105, 102]
start_date='2020-10-14'
stop_date='2020-10-17'

station_json = get_data_from_api_by_station(station_id=station_id, 
                                            start_date=start_date,
                                            stop_date=stop_date)

station_df = transform_json_station_data_to_df(station_json)

/tmp/ipykernel_3689276/3150605319.py:110: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  station_df.groupby('station_id').resample('10T',


In [20]:
station_df.tail()

station_id                date  available_stands  available_bikes  \
427          19 2020-10-16 23:20:00              18.0             12.0   
428          19 2020-10-16 23:30:00              18.0             12.0   
429          19 2020-10-16 23:40:00              18.0             12.0   
430          19 2020-10-16 23:50:00              18.0             12.0   
431          19 2020-10-17 00:00:00              19.0             11.0   

     status  transactions_in  transactions_out  transactions_all  
427     1.0              0.0               0.0               0.0  
428     1.0              0.0               0.0               0.0  
429     1.0              0.0               0.0               0.0  
430     1.0              0.0               0.0               0.0  
431     1.0              0.0               1.0               1.0

In [21]:
station_df.tail()

station_id                date  available_stands  available_bikes  \
427          19 2020-10-16 23:20:00              18.0             12.0   
428          19 2020-10-16 23:30:00              18.0             12.0   
429          19 2020-10-16 23:40:00              18.0             12.0   
430          19 2020-10-16 23:50:00              18.0             12.0   
431          19 2020-10-17 00:00:00              19.0             11.0   

     status  transactions_in  transactions_out  transactions_all  
427     1.0              0.0               0.0               0.0  
428     1.0              0.0               0.0               0.0  
429     1.0              0.0               0.0               0.0  
430     1.0              0.0               0.0               0.0  
431     1.0              0.0               1.0               1.0

In [22]:
station_df.dtypes

station_id                   int64
date                datetime64[ns]
available_stands           float64
available_bikes            float64
status                     float64
transactions_in            float64
transactions_out           float64
transactions_all           float64
dtype: object

### Script

In [25]:
from vcub_keeper.production.data import get_data_from_api_by_station, transform_json_station_data_to_df
from vcub_keeper.transform.features_factory import get_consecutive_no_transactions_out
from vcub_keeper.visualisation import plot_station_activity


In [27]:
station_id=37
#station_id=[19, 105, 102]
start_date='2022-02-01'
stop_date='2022-09'

In [28]:
station_json = get_data_from_api_by_station(station_id=station_id, 
                                            start_date=start_date,
                                            stop_date=stop_date)

station_df = transform_json_station_data_to_df(station_json)

/home/gillesa/github/vcub_keeper/src/vcub_keeper/production/data.py:119: FutureWarning:

'T' is deprecated and will be removed in a future version, please use 'min' instead.



In [29]:
test_df = pd.DataFrame(station_json['data'][0])
test_df.tail(25)

available_bikes  available_stands  id           name  nb_stands  status  \
8355               16                13  37  Jardin Public         30    open   
8356               16                13  37  Jardin Public         30    open   
8357               16                13  37  Jardin Public         30    open   
8358               16                13  37  Jardin Public         30    open   
8359               16                13  37  Jardin Public         30    open   
8360               16                13  37  Jardin Public         30    open   
8361               16                13  37  Jardin Public         30    open   
8362               16                13  37  Jardin Public         30    open   
8363               16                13  37  Jardin Public         30    open   
8364               16                13  37  Jardin Public         30    open   
8365               16                13  37  Jardin Public         30    open   
8366               16                13  37  Jardin Public         30    open   
8367               16                13  37  Jardin Public         30    open   
8368               16                13  37  Jardin Public         30    open   
8369               16                13  37  Jardin Public         30    open   
8370               16                13  37  Jardin Public         30    open   
8371               16                13  37  Jardin Public         30    open   
8372               16                13  37  Jardin Public         30    open   
8373               16                13  37  Jardin Public         30    open   
8374               16                13  37  Jardin Public         30    open   
8375               16                13  37  Jardin Public         30    open   
8376               16                13  37  Jardin Public         30    open   
8377               16                13  37  Jardin Public         30  closed   
8378               16                13  37  Jardin Public         30    open   
8379               15                14  37  Jardin Public         30    open   

                       ts  
8355  2022-09-15T21:57:44  
8356  2022-09-15T22:02:44  
8357  2022-09-15T22:08:44  
8358  2022-09-15T22:14:44  
8359  2022-09-15T22:16:44  
8360  2022-09-15T22:22:44  
8361  2022-09-15T22:27:44  
8362  2022-09-15T22:33:44  
8363  2022-09-15T22:38:44  
8364  2022-09-15T22:43:44  
8365  2022-09-15T22:48:44  
8366  2022-09-15T22:54:44  
8367  2022-09-15T22:56:44  
8368  2022-09-15T23:02:44  
8369  2022-09-15T23:07:44  
8370  2022-09-15T23:12:44  
8371  2022-09-15T23:17:44  
8372  2022-09-15T23:23:44  
8373  2022-09-15T23:28:44  
8374  2022-09-15T23:33:44  
8375  2022-09-15T23:38:44  
8376  2022-09-15T23:44:44  
8377  2022-09-15T23:49:44  
8378  2022-09-15T23:54:44  
8379  2022-09-15T23:56:44

In [30]:
station_df.tail(10)

station_id                date  available_stands  available_bikes  \
32678          37 2022-09-15 22:30:00              13.0             16.0   
32679          37 2022-09-15 22:40:00              13.0             16.0   
32680          37 2022-09-15 22:50:00              13.0             16.0   
32681          37 2022-09-15 23:00:00              13.0             16.0   
32682          37 2022-09-15 23:10:00              13.0             16.0   
32683          37 2022-09-15 23:20:00              13.0             16.0   
32684          37 2022-09-15 23:30:00              13.0             16.0   
32685          37 2022-09-15 23:40:00              13.0             16.0   
32686          37 2022-09-15 23:50:00              13.0             16.0   
32687          37 2022-09-16 00:00:00              14.0             15.0   

       status  transactions_in  transactions_out  transactions_all  
32678     1.0              0.0               0.0               0.0  
32679     1.0              0.0               0.0               0.0  
32680     1.0              0.0               0.0               0.0  
32681     1.0              0.0               0.0               0.0  
32682     1.0              0.0               0.0               0.0  
32683     1.0              0.0               0.0               0.0  
32684     1.0              0.0               0.0               0.0  
32685     1.0              0.0               0.0               0.0  
32686     1.0              0.0               0.0               0.0  
32687     1.0              0.0               1.0               1.0

In [31]:
station_df = get_consecutive_no_transactions_out(station_df) 

In [32]:
station_df

station_id                date  available_stands  available_bikes  \
0              37 2022-02-01 00:10:00               8.0             22.0   
1              37 2022-02-01 00:20:00               8.0             22.0   
2              37 2022-02-01 00:30:00               8.0             22.0   
3              37 2022-02-01 00:40:00               8.0             22.0   
4              37 2022-02-01 00:50:00               8.0             22.0   
...           ...                 ...               ...              ...   
32683          37 2022-09-15 23:20:00              13.0             16.0   
32684          37 2022-09-15 23:30:00              13.0             16.0   
32685          37 2022-09-15 23:40:00              13.0             16.0   
32686          37 2022-09-15 23:50:00              13.0             16.0   
32687          37 2022-09-16 00:00:00              14.0             15.0   

       status  transactions_in  transactions_out  transactions_all  \
0         1.0              0.0               0.0               0.0   
1         1.0              0.0               0.0               0.0   
2         1.0              0.0               0.0               0.0   
3         1.0              0.0               0.0               0.0   
4         1.0              0.0               0.0               0.0   
...       ...              ...               ...               ...   
32683     1.0              0.0               0.0               0.0   
32684     1.0              0.0               0.0               0.0   
32685     1.0              0.0               0.0               0.0   
32686     1.0              0.0               0.0               0.0   
32687     1.0              0.0               1.0               1.0   

       consecutive_no_transactions_out  
0                                    0  
1                                    1  
2                                    2  
3                                    3  
4                                    4  
...                                ...  
32683                                8  
32684                                9  
32685                               10  
32686                               11  
32687                                0  

[32688 rows x 9 columns]

In [34]:
plot_station_activity(station_df, station_id=37, #105 #station_id
                      features_to_plot=['available_bikes', #'available_stands',
                                       'consecutive_no_transactions_out',
                                        'status'
                                       ],
                      #start_date=start_date,
                      #end_date=end_date,
                      return_data=False)

In [35]:
station_df[station_df.status == 0]

station_id                date  available_stands  available_bikes  \
250            37 2022-02-02 17:50:00              23.0              7.0   
251            37 2022-02-02 18:00:00              23.0              7.0   
252            37 2022-02-02 18:10:00              23.0              7.0   
1422           37 2022-02-10 21:10:00              19.0             10.0   
1423           37 2022-02-10 21:20:00              19.0             10.0   
1425           37 2022-02-10 21:40:00              19.0             10.0   
1426           37 2022-02-10 21:50:00              19.0             10.0   
1427           37 2022-02-10 22:00:00              19.0             10.0   
1428           37 2022-02-10 22:10:00              19.0             10.0   
1429           37 2022-02-10 22:20:00              19.0             10.0   
1431           37 2022-02-10 22:40:00              19.0             10.0   
1432           37 2022-02-10 22:50:00              19.0             10.0   
1614           37 2022-02-12 05:10:00              18.0             11.0   
1615           37 2022-02-12 05:20:00              18.0             11.0   
2420           37 2022-02-17 19:30:00              21.0              9.0   
2687           37 2022-02-19 16:00:00              27.0              3.0   
2688           37 2022-02-19 16:10:00              27.0              3.0   
2946           37 2022-02-21 11:10:00              10.0             20.0   
2947           37 2022-02-21 11:20:00              10.0             20.0   
2950           37 2022-02-21 11:50:00              10.0             20.0   
31599          37 2022-09-08 10:40:00               0.0             22.0   
31600          37 2022-09-08 10:50:00               0.0             22.0   
31601          37 2022-09-08 11:00:00               0.0             22.0   
31602          37 2022-09-08 11:10:00               0.0             22.0   
31603          37 2022-09-08 11:20:00               0.0             22.0   
31604          37 2022-09-08 11:30:00               0.0             22.0   
31605          37 2022-09-08 11:40:00               0.0             22.0   
31606          37 2022-09-08 11:50:00               0.0             22.0   
31607          37 2022-09-08 12:00:00               0.0             22.0   
31608          37 2022-09-08 12:10:00               0.0             22.0   
31609          37 2022-09-08 12:20:00               0.0             22.0   
31610          37 2022-09-08 12:30:00               0.0             22.0   
31611          37 2022-09-08 12:40:00               0.0             22.0   
31612          37 2022-09-08 12:50:00               0.0             22.0   
31613          37 2022-09-08 13:00:00               0.0             22.0   
31614          37 2022-09-08 13:10:00               0.0             22.0   
31615          37 2022-09-08 13:20:00               0.0             22.0   
31616          37 2022-09-08 13:30:00               0.0             22.0   
31617          37 2022-09-08 13:40:00               0.0             22.0   
31618          37 2022-09-08 13:50:00               0.0             22.0   
31619          37 2022-09-08 14:00:00               0.0             22.0   
31620          37 2022-09-08 14:10:00               0.0             22.0   
31621          37 2022-09-08 14:20:00               0.0             22.0   
31622          37 2022-09-08 14:30:00               0.0             22.0   
31623          37 2022-09-08 14:40:00               0.0             22.0   
31624          37 2022-09-08 14:50:00               0.0             22.0   
31625          37 2022-09-08 15:00:00               0.0             22.0   
31626          37 2022-09-08 15:10:00               0.0             22.0   
31627          37 2022-09-08 15:20:00               0.0             22.0   
31628          37 2022-09-08 15:30:00               0.0             22.0   
31629          37 2022-09-08 15:40:00               0.0             22.0   
31630          37 2022-09-08 15:50:00               0.0

In [36]:
station_df.status.value_counts()

status
1.0    4044
0.0     151
Name: count, dtype: int64

## API de open data Bordeaux

### Dev

In [37]:
# Day
URL = "https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&&rangeStart=2022-03-31T15:50:00&&rangeEnd=2022-03-31T16:00:00&rangeStep=day"
# 5min
URL = "https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&&rangeStart=2022-03-31T15:50:00&&rangeEnd=2022-03-31T16:00:00&rangeStep=5min"
URL = "https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&&rangeStart=2022-03-31T15:50:00&&rangeEnd=2022-03-31T16:01:00&rangeStep=5min"

# 
URL = "https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&&rangeStart=2022-03-24T15:50:00&&rangeEnd=2022-03-31T16:01:00&rangeStep=5min" # KO
URL = "https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&&rangeStart=2022-03-28&&rangeEnd=2022-03-31&rangeStep=5min" # KO
URL = "https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&&rangeStart=2022-03-30&&rangeEnd=2022-03-31&rangeStep=5min" # KO


# avec filtre station vcub
URL = 'https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&rangeStart=2022-03-31T15:50:00&filter={"ident":2}&rangeEnd=2022-03-31T16:01:00&rangeStep=5min' #OK

# filtre station vcub + 1 semaine data
URL = 'https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&rangeStart=2022-03-24T00:00:00&filter={"ident":2}&rangeEnd=2022-03-31T16:01:00&rangeStep=5min' #OK

# filtre station vcub + 1 semaine data + 1ere données


# 1 +/- semaine de data (toutes stations)
URL = 'https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&rangeStart=2022-03-24T15:50:00&rangeEnd=2022-03-31T16:01:00&rangeStep=5min&attributes=["nom","etat", "ident", "nbplaces", "nbvelos", "gid"]' # KO

# 1 jours de data (toutes stations)
# 17,9 s
URL = 'https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&rangeStart=2022-03-30T15:50:00&rangeEnd=2022-03-31T16:01:00&rangeStep=5min&attributes=["nom","etat", "ident", "nbplaces", "nbvelos", "gid"]' # OK

# 2 jours de data (toutes stations)
# 38,8 s
URL = 'https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&rangeStart=2022-03-30T15:50:00&rangeEnd=2022-03-31T16:01:00&rangeStep=5min&attributes=["nom","etat", "ident", "nbplaces", "nbvelos", "gid"]' # KO

# avec filtre sur plusieurs station vcub
URL = 'https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&rangeStart=2022-03-31T15:50:00&filter={"ident":{"$in":[1,2]}}&rangeEnd=2022-03-31T16:01:00&rangeStep=5min' # OK

# URL optimisé (on choisit les attribut de retour)
attributes=["nom","etat", "ident", "nbplaces", "nbvelos", "gid"]
attributes={"nom": "mode", "etat": "mode", "nbplaces": "max", "nbvelos": "max"}
# 0,4s
URL = 'https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&rangeStart=2022-03-29T15:50:00&filter={"ident":1}&rangeEnd=2022-03-31T16:01:00&rangeStep=5min&attributes=["nom","etat", "ident", "nbplaces", "nbvelos", "gid"]' #OK
# 0,4s
URL = 'https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&rangeStart=2022-03-29T15:50:00&filter={"ident":1}&rangeEnd=2022-03-31T16:01:00&rangeStep=5min&attributes={"nom": "mode", "etat": "mode", "nbplaces": "max", "nbvelos": "max"}' #OK
# 0,7s
URL = 'https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&rangeStart=2022-03-29T15:50:00&filter={"ident":1}&rangeEnd=2022-03-31T16:01:00&rangeStep=5min&' #OK


In [38]:
# Toute les stations sur une période déterminé 

# 1 jours : 18 sec / 53835 lignes
URL = 'https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&rangeStart=2022-03-30T15:50:00&rangeEnd=2022-03-31T16:01:00&rangeStep=5min&attributes={"nom": "mode", "etat": "mode", "nbplaces": "max", "nbvelos": "max"}' #OK

# 2 jours : 37,8 sec --> HS
URL = 'https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&rangeStart=2022-03-29T15:50:00&rangeEnd=2022-03-31T16:01:00&rangeStep=5min&attributes={"nom": "mode", "etat": "mode", "nbplaces": "max", "nbvelos": "max"}' #OK

# 1.5 jours : 30,2 sec --> HS
URL = 'https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&rangeStart=2022-03-29T23:50:00&rangeEnd=2022-03-31T16:01:00&rangeStep=5min&attributes={"nom": "mode", "etat": "mode", "nbplaces": "max", "nbvelos": "max"}' #OK

In [39]:
URL = 'https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&rangeStart=2022-03-24T00:00:00&filter={"ident":2}&rangeEnd=2022-03-31T16:01:00&rangeStep=5min&attributes={"nom": "mode", "etat": "mode", "nbplaces": "max", "nbvelos": "max"}' #OK

Récapitulatif : 

- Pour les requêtes d'affichage d'une station (avec graph + anomalie) :
    Possibilité d'utiliser une requête de ce type qui est assez rapide (+/- 1 sec)
   
    `URL = 'https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&rangeStart=2022-03-24T00:00:00&filter={"ident":2}&rangeEnd=2022-03-31T16:01:00&rangeStep=5min&attributes={"nom": "mode", "etat": "mode", "nbplaces": "max", "nbvelos": "max"}'`

- Pour les requêtes lors de la détection d'ano toutes les 10 minutes : 
    On ne peut pas utiliser la même requête que plus haut sans filtre de stations (pas de retour de la requête / trop long / limitation API). Par contre il est possible de demander +/- 24h de données pour toutes les stations (+/- 18 sec)
    
    `URL = 'https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=[KEY]&rangeStart=2022-03-30T15:50:00&rangeEnd=2022-03-31T16:01:00&rangeStep=5min&attributes={"nom": "mode", "etat": "mode", "nbplaces": "max", "nbvelos": "max"}'`


In [40]:
response = requests.get(URL)
response

<Response [403]>

In [536]:
response.json()
#{"nom": "mode", "etat": "mode", "nbplaces": "max", "nbvelos": "max"}

{'error': "Erreur interne. Si le problème persiste contactez l'administrateur"}

In [533]:
len(response.json()['features'])

2124

In [523]:
# Create Df with data in list
station_df = pd.json_normalize(response.json(), record_path =['features'])

# Naming
station_df.rename(columns={'properties.time':'time'}, inplace=True)
station_df.rename(columns={'properties.gid':'gid'}, inplace=True)
station_df.rename(columns={'properties.nom':'nom'}, inplace=True)
station_df.rename(columns={'properties.etat':'etat'}, inplace=True)
station_df.rename(columns={'properties.nbplaces':'nbplaces'}, inplace=True)
station_df.rename(columns={'properties.nbvelos':'nbvelos'}, inplace=True)

try :
# type 
    station_df['time'] = pd.to_datetime(station_df['time'])
except:
# AVEC backintime
    station_df['mdate'] = pd.to_datetime(station_df['mdate'])
    station_df.rename(columns={'mdate':'time'}, inplace=True)

In [524]:
station_df.time.unique()

array([datetime.datetime(2022, 3, 25, 0, 0, tzinfo=tzoffset(None, 3600)),
       datetime.datetime(2022, 3, 25, 0, 5, tzinfo=tzoffset(None, 3600)),
       datetime.datetime(2022, 3, 25, 0, 10, tzinfo=tzoffset(None, 3600)),
       ...,
       datetime.datetime(2022, 4, 1, 9, 45, tzinfo=tzoffset(None, 7200)),
       datetime.datetime(2022, 4, 1, 9, 50, tzinfo=tzoffset(None, 7200)),
       datetime.datetime(2022, 4, 1, 9, 55, tzinfo=tzoffset(None, 7200))],
      dtype=object)

In [525]:
station_df.time.min(), station_df.time.max()

(datetime.datetime(2022, 3, 25, 0, 0, tzinfo=tzoffset(None, 3600)),
 datetime.datetime(2022, 4, 1, 9, 55, tzinfo=tzoffset(None, 7200)))

In [526]:
station_df.tail(45)

type                       time  gid       nom       etat  nbplaces  \
2079  Feature  2022-04-01 06:15:00+02:00    2  St Bruno  CONNECTEE         8   
2080  Feature  2022-04-01 06:20:00+02:00    2  St Bruno  CONNECTEE         8   
2081  Feature  2022-04-01 06:25:00+02:00    2  St Bruno  CONNECTEE         8   
2082  Feature  2022-04-01 06:30:00+02:00    2  St Bruno  CONNECTEE         8   
2083  Feature  2022-04-01 06:35:00+02:00    2  St Bruno  CONNECTEE         8   
2084  Feature  2022-04-01 06:40:00+02:00    2  St Bruno  CONNECTEE         8   
2085  Feature  2022-04-01 06:45:00+02:00    2  St Bruno  CONNECTEE         8   
2086  Feature  2022-04-01 06:50:00+02:00    2  St Bruno  CONNECTEE         8   
2087  Feature  2022-04-01 06:55:00+02:00    2  St Bruno  CONNECTEE         9   
2088  Feature  2022-04-01 07:00:00+02:00    2  St Bruno  CONNECTEE         9   
2089  Feature  2022-04-01 07:05:00+02:00    2  St Bruno  CONNECTEE         9   
2090  Feature  2022-04-01 07:10:00+02:00    2  St Bruno  CONNECTEE         9   
2091  Feature  2022-04-01 07:15:00+02:00    2  St Bruno  CONNECTEE         9   
2092  Feature  2022-04-01 07:20:00+02:00    2  St Bruno  CONNECTEE         9   
2093  Feature  2022-04-01 07:25:00+02:00    2  St Bruno  CONNECTEE         9   
2094  Feature  2022-04-01 07:30:00+02:00    2  St Bruno  CONNECTEE         9   
2095  Feature  2022-04-01 07:35:00+02:00    2  St Bruno  CONNECTEE         8   
2096  Feature  2022-04-01 07:40:00+02:00    2  St Bruno  CONNECTEE         9   
2097  Feature  2022-04-01 07:45:00+02:00    2  St Bruno  CONNECTEE         9   
2098  Feature  2022-04-01 07:50:00+02:00    2  St Bruno  CONNECTEE         8   
2099  Feature  2022-04-01 07:55:00+02:00    2  St Bruno  CONNECTEE         8   
2100  Feature  2022-04-01 08:00:00+02:00    2  St Bruno  CONNECTEE         8   
2101  Feature  2022-04-01 08:05:00+02:00    2  St Bruno  CONNECTEE         8   
2102  Feature  2022-04-01 08:10:00+02:00    2  St Bruno  CONNECTEE         8   
2103  Feature  2022-04-01 08:15:00+02:00    2  St Bruno  CONNECTEE         8   
2104  Feature  2022-04-01 08:20:00+02:00    2  St Bruno  CONNECTEE         8   
2105  Feature  2022-04-01 08:25:00+02:00    2  St Bruno  CONNECTEE         8   
2106  Feature  2022-04-01 08:30:00+02:00    2  St Bruno  CONNECTEE        10   
2107  Feature  2022-04-01 08:35:00+02:00    2  St Bruno  CONNECTEE        10   
2108  Feature  2022-04-01 08:40:00+02:00    2  St Bruno  CONNECTEE        10   
2109  Feature  2022-04-01 08:45:00+02:00    2  St Bruno  CONNECTEE        10   
2110  Feature  2022-04-01 08:50:00+02:00    2  St Bruno  CONNECTEE        10   
2111  Feature  2022-04-01 08:55:00+02:00    2  St Bruno  CONNECTEE        10   
2112  Feature  2022-04-01 09:00:00+02:00    2  St Bruno  CONNECTEE         9   
2113  Feature  2022-04-01 09:05:00+02:00    2  St Bruno  CONNECTEE         9   
2114  Feature  2022-04-01 09:10:00+02:00    2  St Bruno  CONNECTEE        10   
2115  Feature  2022-04-01 09:15:00+02:00    2  St Bruno  CONNECTEE        10   
2116  Feature  2022-04-01 09:20:00+02:00    2  St Bruno  CONNECTEE        10   
2117  Feature  2022-04-01 09:25:00+02:00    2  St Bruno  CONNECTEE        10   
2118  Feature  2022-04-01 09:30:00+02:00    2  St Bruno  CONNECTEE        11   
2119  Feature  2022-04-01 09:35:00+02:00    2  St Bruno  CONNECTEE        11   
2120  Feature  2022-04-01 09:40:00+02:00    2  St Bruno  CONNECTEE        10   
2121  Feature  2022-04-01 09:45:00+02:00    2  St Bruno  CONNECTEE        10   
2122  Feature  2022-04-01 09:50:00+02:00    2  St Bruno  CONNECTEE        10   
2123  Feature  2022-04-01 09:55:00+02:00    2  St Bruno  CONNECTEE        10   

      nbvelos  
2079       12  
2080       12  
2081       12  
2082       12  
2083       12  
2084       12  
2085       12  
2086       12  
2087       12  
2088       11  
2089       11  
2090       11  
2091       11  
2092       11  
2093       11  
2094       12  
2095       12  
2096       12  
2097       12  
2098    

In [527]:
station_df.gid.nunique()

1

In [529]:
response.json()['features'][0]['properties']

{'time': '2022-03-25T00:00:00+01:00',
 'gid': 2,
 'nom': 'St Bruno',
 'etat': 'CONNECTEE',
 'nbplaces': 10,
 'nbvelos': 10}

### Industrialisation

In [41]:
def get_data_from_api_bdx_by_station(station_id, start_date, stop_date):
    """
    Permet d'obtenir les données d'activité d'une station via une API d'open data Bordeaux
    
    Parameters
    ----------
    station_id : Int or List
        Numéro de la station de Vcub
    start_date : str
        Date de début de la Time Serie
    stop_date : str
        Date de fin de la Time Serie
    
    Returns
    -------
    Time serie in Json format
        
    Examples
    --------
    station_json = get_data_from_api_bdx_by_station(station_id=19, 
                                                    start_date='2020-10-14',
                                                    stop_date='2020-10-17')
    """
    
    # Si plusieurs station_id ([124,  15,  60,])
    if isinstance(station_id, (list, np.ndarray)):
        station_id = ','.join(map(str, station_id))

        url = \
            'https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=' + KEY_API_BDX + '&rangeStart=' + str(start_date) +\
                '&filter={"ident":{"$in":[' + str(station_id) +']}}&rangeEnd=' + str(stop_date) +\
                '&rangeStep=5min&attributes={"nom": "mode", "etat": "mode", "nbplaces": "max", "nbvelos": "max"}'
    # Si une seul station_id
    else:
        url = \
            'https://data.bordeaux-metropole.fr/geojson/aggregate/ci_vcub_p?key=' + KEY_API_BDX + '&rangeStart=' + str(start_date) +\
                '&filter={"ident":' + str(station_id) +'}&rangeEnd=' + str(stop_date) +\
                '&rangeStep=5min&attributes={"nom": "mode", "etat": "mode", "nbplaces": "max", "nbvelos": "max"}'


    response = requests.get(url)
    return response.json()

def transform_json_api_bdx_station_data_to_df(station_json):
    """
    Tranforme la Time Serie d'activité d'une ou plusieurs station en DataFrame
    à partir de la fonction get_data_from_api_bdx_by_station()
    Effectue plusieurs transformation comme la fonction create/creator.py 
    create_activity_time_series()
        - Naming des colonnes json
        - Structuration
        - Naming
        - Ajout de variables
        - Resampling sur 10min
    
    Parameters
    ----------
    station_json : json
        Time serie au format json de l'activité d'une station (ou plusieurs)
    Returns
    -------
    station_df_resample : DataFrame
        Time serie au format DataFrame de l'activité d'une ou plusieurs station
        resampler sur 10 min.
        
    Examples
    --------
    
    station_df = transform_json_api_bdx_station_data_to_df(station_json)
    
    """

    station_df = pd.json_normalize(station_json, record_path =['features'])

    # Naming from JSON DataFrame
    station_df.rename(columns={'properties.time':'time'}, inplace=True)
    station_df.rename(columns={'properties.gid':'gid'}, inplace=True)
    station_df.rename(columns={'properties.nom':'nom'}, inplace=True)
    station_df.rename(columns={'properties.etat':'etat'}, inplace=True)
    station_df.rename(columns={'properties.nbplaces':'nbplaces'}, inplace=True)
    station_df.rename(columns={'properties.nbvelos':'nbvelos'}, inplace=True)

    # naming api Bdx to vanilla api (get_data_from_api_by_station) from DataFrame
    # Naming
    station_df.rename(columns={'time':'date'}, inplace=True)
    station_df.rename(columns={'gid':'station_id'}, inplace=True)
    station_df.rename(columns={'nom':'name'}, inplace=True)
    station_df.rename(columns={'etat':'status'}, inplace=True)
    station_df.rename(columns={'nbvelos':'available_bikes'}, inplace=True)
    station_df.rename(columns={'nbplaces':'available_stands'}, inplace=True)

    # Status mapping
    status_dict = {'CONNECTEE' : 1,
                   'DECONNECTEE' : 0}
    station_df['status'] = station_df['status'].map(status_dict)
    station_df['status'] = station_df['status'].astype('uint8')

    # Casting & sorting DataFrame on station_id & date
    station_df['date'] = pd.to_datetime(station_df['date'])
    try:
        station_df['date'] = \
            pd.to_datetime(station_df['date'])
    except: # Changemnent d'horraire https://github.com/armgilles/vcub_watcher/issues/44
        station_df['date'] = \
            pd.to_datetime(station_df['date'], utc=True)
    try:
        station_df['date'] = \
            station_df['date'].dt.tz_localize('Europe/Paris')
    except:  # try to convert TZ
        station_df['date'] = \
            station_df['date'].dt.tz_convert('Europe/Paris')

    station_df['station_id'] = station_df['station_id'].astype(int)
    station_df = station_df.sort_values(['station_id', 'date'], ascending=[1, 1])

    # Reset index
    station_df = station_df.reset_index(drop=True)

    # Dropduplicate station_id / date rows
    station_df = station_df.drop_duplicates(subset=['station_id', 'date']).reset_index(drop=True)

    # Create features
    station_df = get_transactions_in(station_df)
    station_df = get_transactions_out(station_df)
    station_df = get_transactions_all(station_df)

    ## Resampling

    # # cf Bug Pandas : https://github.com/pandas-dev/pandas/issues/33548
    station_df = station_df.set_index('date')

    station_df_resample = \
    station_df.groupby('station_id').resample('10T', 
                                                label='right',
                                                ).agg({'available_stands' : 'last',
                                                       'available_bikes' : 'last',
                                                       'status' : 'max', # Empeche les micro déconnection à la station
                                                       'transactions_in' : 'sum',
                                                       'transactions_out' : 'sum',
                                                       'transactions_all' : 'sum'}).reset_index()
    return station_df_resample

In [26]:
from vcub_keeper.production.data import get_data_from_api_bdx_by_station, transform_json_api_bdx_station_data_to_df

In [8]:
station_id=1
# station_id=[124,  15,  60,]
# statoin_id = [124,  15,  60,  18,  10,  68, 130,   2, 105, 120,  11, 110,   9,
#         23,   3,  16,  20, 136,  42,  21, 131,  59,  45, 172,   6,  24,
#         36, 108,  19, 125, 135,  37, 139,  99,  28,  57,   7,  98,   8,
#         41,  40,  58,  55, 109,   1,   4, 100, 134, 174, 101,  56, 104,
#         43,  54,  44, 102, 133, 103,   5, 127,  65,  22, 123,  39, 106]
start_date='2022-03-24'
stop_date='2022-04-02'

In [9]:
from datetime import timedelta, date

# Get date
date_today = date.today()
end_date = date_today + timedelta(days=1)
start_date = date_today - timedelta(days=8)

start_date_str = start_date.strftime('%Y-%m-%d')
end_date_str = end_date.strftime('%Y-%m-%d')
print(start_date_str, end_date_str)

2024-09-09 2024-09-18


In [10]:
station_json = get_data_from_api_bdx_by_station(station_id=station_id, 
                                                start_date=start_date,
                                                stop_date=end_date_str)

station_df = transform_json_api_bdx_station_data_to_df(station_json)

In [15]:
station_df

station_id                      date  available_stands  available_bikes  \
0            106 2023-07-03 02:10:00+02:00                37                1   
1            106 2023-07-03 02:20:00+02:00                36                2   
2            106 2023-07-03 02:30:00+02:00                36                2   
3            106 2023-07-03 02:40:00+02:00                36                2   
4            106 2023-07-03 02:50:00+02:00                36                2   
...          ...                       ...               ...              ...   
4459         106 2023-08-03 01:20:00+02:00                16               24   
4460         106 2023-08-03 01:30:00+02:00                16               24   
4461         106 2023-08-03 01:40:00+02:00                16               24   
4462         106 2023-08-03 01:50:00+02:00                16               24   
4463         106 2023-08-03 02:00:00+02:00                16               26   

      status  transactions_in  transactions_out  transactions_all  
0          1              0.0               0.0               0.0  
1          1              1.0               0.0               1.0  
2          1              0.0               0.0               0.0  
3          1              0.0               0.0               0.0  
4          1              0.0               0.0               0.0  
...      ...              ...               ...               ...  
4459       1              0.0               0.0               0.0  
4460       1              0.0               0.0               0.0  
4461       1              0.0               0.0               0.0  
4462       1              0.0               0.0               0.0  
4463       1              2.0               0.0               2.0  

[4464 rows x 8 columns]

In [16]:
station_id = 106
start_date = "2023-07-03"
stop_date = "2023-08-03"

station_json = get_data_from_api_bdx_by_station(station_id=station_id, start_date=start_date, stop_date=stop_date)

station_df = transform_json_api_bdx_station_data_to_df(station_json)

In [17]:
station_df.groupby("station_id", as_index=False)["date"].min()

station_id                      date
0         106 2023-07-03 02:10:00+02:00

In [18]:
assert station_df["station_id"].nunique() == 1
assert station_df["station_id"].unique() == [106]

In [27]:
import json
from vcub_keeper.config import ROOT_TESTS_DATA

station_id = "106"
start_date = "2023-03-10"
stop_date = "2023-03-11"

station_json = get_data_from_api_bdx_by_station(station_id=station_id, start_date=start_date, stop_date=stop_date)

# Loading data from data test
with open(ROOT_TESTS_DATA + "data_test_api_from_bdx.json") as f:
    station_json_loaded = json.load(f)

In [33]:
df_loaded = pd.json_normalize(station_json_loaded, record_path=["features"])
df_loaded.head()

type            properties.time  properties.gid        properties.nom  \
0  Feature  2023-03-10T01:00:00+01:00             106  Place de la Victoire   
1  Feature  2023-03-10T01:05:00+01:00             106  Place de la Victoire   
2  Feature  2023-03-10T01:10:00+01:00             106  Place de la Victoire   
3  Feature  2023-03-10T01:15:00+01:00             106  Place de la Victoire   
4  Feature  2023-03-10T01:20:00+01:00             106  Place de la Victoire   

  properties.etat  properties.nbplaces  properties.nbvelos  
0       CONNECTEE                   32                   8  
1       CONNECTEE                   32                   8  
2       CONNECTEE                   32                   8  
3       CONNECTEE                   32                   8  
4       CONNECTEE                   32                   8

In [34]:
df = pd.json_normalize(station_json, record_path=["features"])
df.head()

type            properties.time  properties.gid  properties.ident  \
0  Feature  2023-03-10T01:00:00+01:00             106               106   
1  Feature  2023-03-10T01:05:00+01:00             106               106   
2  Feature  2023-03-10T01:10:00+01:00             106               106   
3  Feature  2023-03-10T01:15:00+01:00             106               106   
4  Feature  2023-03-10T01:20:00+01:00             106               106   

         properties.nom properties.etat  properties.nbplaces  \
0  Place de la Victoire       CONNECTEE                   32   
1  Place de la Victoire       CONNECTEE                   32   
2  Place de la Victoire       CONNECTEE                   32   
3  Place de la Victoire       CONNECTEE                   32   
4  Place de la Victoire       CONNECTEE                   32   

   properties.nbvelos  
0                   8  
1                   8  
2                   8  
3                   8  
4                   8

### Test de rapidité API Open Data VS Oslandia

In [17]:
def test_api_bdx(station_id=station_id, start_date=start_date, stop_date=stop_date):
    """
    """
    station_json = get_data_from_api_bdx_by_station(station_id=station_id, 
                                                start_date=start_date,
                                                stop_date=stop_date)

    station_df = transform_json_api_bdx_station_data_to_df(station_json)
    return station_df


from vcub_keeper.production.data import (get_data_from_api_by_station,
                                         transform_json_station_data_to_df)
from vcub_keeper.transform.features_factory import get_consecutive_no_transactions_out
from vcub_keeper.visualisation import *

def test_api_oslandia(station_id=station_id, start_date=start_date, stop_date=stop_date):
    """
    """
    station_json = get_data_from_api_by_station(station_id=station_id, 
                                            start_date=start_date,
                                            stop_date=stop_date)

    station_df = transform_json_station_data_to_df(station_json)
    return station_df

#### Test de perf data pour une station sur une semaine

In [23]:
station_id=2
start_date='2022-03-24'
stop_date='2022-04-02'

In [24]:
# 1.16 s ± 74.7 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
%timeit test_api_bdx(station_id=station_id, start_date=start_date, stop_date=stop_date)

1.16 s ± 74.7 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [25]:
# TO do en attendant que le serveur Oslandia soit UP
%timeit test_api_oslandia(station_id=station_id, start_date=start_date, stop_date=stop_date)

JSONDecodeError: Expecting value: line 1 column 1 (char 0)

#### Test de perf data pour plusieurs stations sur une semaine

In [27]:
statoin_id = [124,  15,  60,  18,  10,  68, 130,   2, 105, 120,  11, 110,   9,
        23,   3,  16,  20, 136,  42,  21, 131,  59,  45, 172,   6,  24,
        36, 108,  19, 125, 135,  37, 139,  99,  28,  57,   7,  98,   8,
        41,  40,  58,  55, 109,   1,   4, 100, 134, 174, 101,  56, 104,
        43,  54,  44, 102, 133, 103,   5, 127,  65,  22, 123,  39, 106]
start_date='2022-03-24'
stop_date='2022-04-02'

In [28]:
# 3.1 s ± 182 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
%timeit test_api_bdx(station_id=station_id, start_date=start_date, stop_date=stop_date)

1.16 s ± 70.2 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [29]:
# TO do en attendant que le serveur Oslandia soit UP
%timeit test_api_oslandia(station_id=station_id, start_date=start_date, stop_date=stop_date)

JSONDecodeError: Expecting value: line 1 column 1 (char 0)